# Setup
Install basic dependenciesx

In [184]:
import pandas as pd
import numpy as np
from IPython.display import Markdown, display


# Display settings for pandas
pd.set_option('display.max_columns', 100)
pd.set_option('display.max_rows', 100)
pd.set_option('display.float_format', '{:.4f}'.format)


How many students per team?

In [185]:
STUDENTS_PER_TEAM = 5

A blank dataframe that will hold each student's assigned project

In [186]:
df_assignments = pd.DataFrame(columns=['email', 'project'])

## Open data file

In [187]:
df_votes = pd.read_csv('data/project_preferences_fall2025.csv')


Simplify column names and remove unnecessary columns.

In [188]:
df_votes = df_votes.rename(columns={
    'Email Address': 'email',
    'First choice': 'first',
    'Second choice': 'second',
    'Third choice': 'third',
    'Are any of these choices your own project proposal?': 'voted_for_self'
})[['email', 'first', 'second', 'third', 'voted_for_self']]

Remove all before a dash and trim whitespace.

In [189]:
for col in ['first', 'second', 'third']:
    df_votes[col] = df_votes[col].str.split('-').str[0].str.strip()

Convert all project names to lowercase.

In [190]:
for col in ['first', 'second', 'third']:
    df_votes[col] = df_votes[col].str.lower()

In [191]:
df_votes.sample(5)

email               first       second           third  \
115  sm10454@nyu.edu          nourishpet  gymflow nyu  kitchen helper   
14    av3114@nyu.edu         roulette go     strideai        strideai   
113   sj3915@nyu.edu  cash me if you can   cartranker        strideai   
27   esv2020@nyu.edu            dinewise     sanpvite            rirf   
116   mnm497@nyu.edu                rirf   nutrismart     careconnect   

                                        voted_for_self  
115                                 Yes - First choice  
14   No - I did not select my own project proposal ...  
113                                 Yes - First choice  
27                                 Yes - Second choice  
116                                 Yes - First choice

## Determine project names

In [192]:
project_names = pd.Series(pd.unique(df_votes[['first', 'second', 'third']].values.ravel()))

In [193]:
project_names = project_names.str.lower()

In [194]:
project_names.describe()

count             52
unique            52
top       rendezvous
freq               1
dtype: object

In [195]:
project_names.sample(3)

2      next quad
14    instaskill
46          home
dtype: object

## Count votes

Total number of first, second, and third choice votes for each project.

In [196]:
def get_remaining_vote_counts(df_votes):
    vote_counts = pd.DataFrame({
        'project': project_names,
        'first_count': [df_votes['first'].str.lower().eq(name).sum() for name in project_names],
        'second_count': [df_votes['second'].str.lower().eq(name).sum() for name in project_names],
        'third_count': [df_votes['third'].str.lower().eq(name).sum() for name in project_names]
    })
    vote_counts['total'] = vote_counts['first_count'] + vote_counts['second_count'] + vote_counts['third_count']

    vote_counts.sort_values(
        by=['first_count', 'second_count', 'third_count'],
        ascending=[False, False, False]
    )
    return vote_counts

In [197]:
vote_counts = get_remaining_vote_counts(df_votes)
vote_counts

project  first_count  second_count  third_count  total
0                  rendezvous            4             1            7     12
1                         tbd            0             2            2      4
2                   next quad            4             4            0      8
3              kitchen helper            1             0            1      2
4                 commyounity            3             2            5     10
5    study space finder @ nyu            3             6            4     13
6                 careconnect            2             1            1      4
7                  cartranker            1             3            3      7
8        cardwise automations            2             5            2      9
9                pocketbudget            3             3            2      8
10                  tasklatte            2             2            7     11
11                roulette go            3             2            1      6
12                 moodsphere            5             2            1      8
13                gesturetalk            5             4            6     15
14                 instaskill            4             4            4     12
15                 vodtracker            0             4            1      5
16                 nourishpet            8             5            3     16
17                   agrilink            3             0            2      5
18                tickerpickr            3             5            2     10
19                    fishdex            1             1            1      3
20          the language café            2             3            3      8
21                   dinewise            1             3            2      6
22  dungeons and distractions            2             1            3      6
23                    swapbay            5             2            1      8
24                       camp            5             4            0      9
25                  roomiehub            2             8            2     12
26                 nutrismart            3            11            2     16
27               project crux            1             1            3      5
28                   strideai            4             1            5     10
29                gymflow nyu            0             3            8     11
30              campusconnect            1             0            2      3
31                      spin!            1             2            1      4
32                   taskbank            5             0            1      6
33                 engage 2.0            0             1            2      3
34         cash me if you can            4             1            4      9
35                   toberead            3             2            1      6
36                    upstore            3             2            1      6
37                   sanpvite            0             1            1      2
38                       rirf            1             0            6      7
39                   profpick            2             3            1      6
40                       musi            4             7            1     12
41                   supermix            2             1            3      6
42                   einstein            3             2            2      7
43                over budget            0             2            1      3
44         flavors & fortunes            0             0            1      1
45                    stashly            2             0            1      3
46                       home            1             0            0      1
47              savings quest            0             1            2      3
48                     ascend            1             1            0      2
49                     fithub            4             0            0      4
50                  studymeta            0             0            3      3
51     campus reso

Identify projects with insufficient votes

In [198]:
# Identify projects with insufficient total votes
vote_counts = get_remaining_vote_counts(df_votes)
insufficient_projects = vote_counts[vote_counts['total'] < STUDENTS_PER_TEAM][['project', 'total']]
insufficient_projects


project  total
1                      tbd      4
3           kitchen helper      2
6              careconnect      4
19                 fishdex      3
30           campusconnect      3
31                   spin!      4
33              engage 2.0      3
37                sanpvite      2
43             over budget      3
44      flavors & fortunes      1
45                 stashly      3
46                    home      1
47           savings quest      3
48                  ascend      2
49                  fithub      4
50               studymeta      3
51  campus resource finder      1

Remove those projects with insufficient votes from the vote counts.

In [199]:

# Remove these projects from vote_counts
vote_counts = vote_counts[~vote_counts['project'].isin(insufficient_projects['project'])].reset_index(drop=True)
vote_counts

project  first_count  second_count  third_count  total
0                  rendezvous            4             1            7     12
1                   next quad            4             4            0      8
2                 commyounity            3             2            5     10
3    study space finder @ nyu            3             6            4     13
4                  cartranker            1             3            3      7
5        cardwise automations            2             5            2      9
6                pocketbudget            3             3            2      8
7                   tasklatte            2             2            7     11
8                 roulette go            3             2            1      6
9                  moodsphere            5             2            1      8
10                gesturetalk            5             4            6     15
11                 instaskill            4             4            4     12
12                 vodtracker            0             4            1      5
13                 nourishpet            8             5            3     16
14                   agrilink            3             0            2      5
15                tickerpickr            3             5            2     10
16          the language café            2             3            3      8
17                   dinewise            1             3            2      6
18  dungeons and distractions            2             1            3      6
19                    swapbay            5             2            1      8
20                       camp            5             4            0      9
21                  roomiehub            2             8            2     12
22                 nutrismart            3            11            2     16
23               project crux            1             1            3      5
24                   strideai            4             1            5     10
25                gymflow nyu            0             3            8     11
26                   taskbank            5             0            1      6
27         cash me if you can            4             1            4      9
28                   toberead            3             2            1      6
29                    upstore            3             2            1      6
30                       rirf            1             0            6      7
31                   profpick            2             3            1      6
32                       musi            4             7            1     12
33                   supermix            2             1            3      6
34                   einstein            3             2            2      7

Remove mention of those projects from df_votes.

In [200]:
for project in insufficient_projects:
    for col in ['first', 'second', 'third']:
        df_votes.loc[df_votes[col] == project, col] = np.nan

df_votes.sample(10)


email              first                    second  \
57   ns5745@nyu.edu          next quad               gesturetalk   
31  acc7936@nyu.edu               musi  study space finder @ nyu   
29  aib6932@nyu.edu        tickerpickr                  profpick   
13  ab11475@nyu.edu            swapbay                      camp   
69   wc2184@nyu.edu           taskbank                vodtracker   
94   dy2262@nyu.edu               musi                nourishpet   
14   av3114@nyu.edu        roulette go                  strideai   
67   sg7335@nyu.edu           einstein                      musi   
20   at4933@nyu.edu  the language café              pocketbudget   
99   lj2410@nyu.edu        commyounity                  profpick   

                        third  \
57                       rirf   
31                gymflow nyu   
29                commyounity   
13                commyounity   
69                  studymeta   
94  dungeons and distractions   
14                   strideai   
67                   supermix   
20                   taskbank   
99                      spin!   

                                       voted_for_self  
57                                 Yes - First choice  
31  No - I did not select my own project proposal ...  
29                                 Yes - First choice  
13                                 Yes - First choice  
69                                 Yes - Third choice  
94  No - I did not select my own project proposal ...  
14  No - I did not select my own project proposal ...  
67                                 Yes - First choice  
20                                 Yes - First choice  
99  No - I did not select my own project proposal ...

## Easy teams to form based on first choices
Make teams from projects where exactly the number of students voted for a project who are necessary to form a complete team.

In [201]:
df_easy_formation = vote_counts[
    (vote_counts['first_count'] % STUDENTS_PER_TEAM == 0) & 
    (vote_counts['first_count'] > 0)
][['project', 'first_count']]
df_easy_formation

project  first_count
9    moodsphere            5
10  gesturetalk            5
19      swapbay            5
20         camp            5
26     taskbank            5

In [202]:
# Find projects that are easy to form teams for
easy_projects = set(df_easy_formation['project'])

# Select rows in df_votes where 'first' matches an easy project
mask = df_votes['first'].isin(easy_projects)
matched_rows = df_votes[mask][['email', 'first']].rename(columns={'first': 'project'})

# Add these assignments to df_assignments
df_assignments = pd.concat([df_assignments, matched_rows], ignore_index=True)

# Remove assigned students from df_votes
df_votes = df_votes[~mask].reset_index(drop=True)
df_assignments

email      project
0    pgl8973@nyu.edu   moodsphere
1    wht7519@nyu.edu  gesturetalk
2    and8979@nyu.edu      swapbay
3    ab11475@nyu.edu      swapbay
4    hbm9834@nyu.edu      swapbay
5    sad9798@nyu.edu      swapbay
6     sd5135@nyu.edu   moodsphere
7     cp3588@nyu.edu  gesturetalk
8   amp10098@nyu.edu   moodsphere
9    asm8879@nyu.edu         camp
10    jf4654@nyu.edu  gesturetalk
11   ak10747@nyu.edu         camp
12    tc3661@nyu.edu  gesturetalk
13    sb8520@nyu.edu   moodsphere
14    si2356@nyu.edu         camp
15    br2412@nyu.edu  gesturetalk
16    ks7118@nyu.edu      swapbay
17    wc2184@nyu.edu     taskbank
18    mn3497@nyu.edu         camp
19   sk10741@nyu.edu         camp
20   sk11019@nyu.edu     taskbank
21    sp7007@nyu.edu     taskbank
22   ss17894@nyu.edu     taskbank
23   ab11578@nyu.edu     taskbank
24   sar9165@nyu.edu   moodsphere

## Sort candidates for each remaining project and assign teams
Iterate through projects and sort people by vote priority.

In [203]:
# iterate through each project
for _, row in vote_counts.iterrows():
    project = row['project']

    # create a dataframe of those who voted on it as first choice
    df_project_votes = df_votes[
        (df_votes['first'] == project) |
        (df_votes['second'] == project) |
        (df_votes['third'] == project)
    ]

    # sort by those who voted for it as first, second, third choice
    df_project_votes = df_project_votes.assign(
        sort_priority=np.select(
            [
                # first choice
                (df_project_votes['first'] == project) & (df_project_votes['voted_for_self'] == 'Yes - First choice'),
                (df_project_votes['first'] == project) & (df_project_votes['voted_for_self'] != 'Yes - First choice'),
                # second choice
                (df_project_votes['second'] == project) & (df_project_votes['voted_for_self'] == 'Yes - Second choice'),
                (df_project_votes['second'] == project) & (df_project_votes['voted_for_self'] != 'Yes - Second choice'),
                # third choice
                (df_project_votes['third'] == project) & (df_project_votes['voted_for_self'] == 'Yes - Third choice'),
                (df_project_votes['third'] == project) & (df_project_votes['voted_for_self'] != 'Yes - Third choice')
            ],
            [6, 5, 4, 3, 2, 1],
            default=0
        )
    ).sort_values(by='sort_priority', ascending=False).reset_index(drop=True)

    # print out for debugging
    display(Markdown(f"### Project '{project}'"))
    display(df_project_votes)

    # assign students to remaining projects, as long as there are sufficient students who voted for them
    if len(df_project_votes) >= STUDENTS_PER_TEAM:
        selected = df_project_votes.iloc[:STUDENTS_PER_TEAM]
        new_assignments = selected[['email']].copy()
        new_assignments['project'] = project
        # store the assignments for this team
        df_assignments = pd.concat([df_assignments, new_assignments], ignore_index=True)
        df_votes = df_votes[~df_votes['email'].isin(selected['email'])].reset_index(drop=True)

    # iterate to the next project...

### Project 'rendezvous'

email                     first             second  \
0    nb3733@nyu.edu                rendezvous          tasklatte   
1   dhh5829@nyu.edu                rendezvous            upstore   
2    yz6926@nyu.edu                rendezvous                tbd   
3    sp7298@nyu.edu                rendezvous          roomiehub   
4   jc11678@nyu.edu                 tasklatte         rendezvous   
5    ci2106@nyu.edu               commyounity          next quad   
6    so2426@nyu.edu                   upstore  the language café   
7    st4850@nyu.edu                 tasklatte      savings quest   
8   jl12397@nyu.edu                nourishpet               musi   
9   prc9852@nyu.edu  study space finder @ nyu        roulette go   
10   zs2838@nyu.edu                 next quad         nourishpet   
11   vp2306@nyu.edu               commyounity        tickerpickr   

                       third  \
0   study space finder @ nyu   
1                gesturetalk   
2                        tbd   
3              savings quest   
4         flavors & fortunes   
5                 rendezvous   
6                 rendezvous   
7                 rendezvous   
8                 rendezvous   
9                 rendezvous   
10                rendezvous   
11                rendezvous   

                                       voted_for_self  sort_priority  
0                                  Yes - First choice              6  
1                                  Yes - First choice              6  
2   No - I did not select my own project proposal ...              5  
3                                  Yes - Third choice              5  
4                                  Yes - Third choice              3  
5                                  Yes - First choice              1  
6                                  Yes - First choice              1  
7                                  Yes - First choice              1  
8   No - I did not select my own project proposal ...              1  
9   No - I did not select my own project proposal ...              1  
10                                 Yes - First choice              1  
11                                Yes - Second choice              1

### Project 'next quad'

email        first       second       third      voted_for_self  \
0  cb5330@nyu.edu    next quad          tbd         tbd  Yes - First choice   
1  ns5745@nyu.edu    next quad  gesturetalk        rirf  Yes - First choice   
2  zs2838@nyu.edu    next quad   nourishpet  rendezvous  Yes - First choice   
3  hs5312@nyu.edu    next quad   instaskill        musi  Yes - First choice   
4  ci2106@nyu.edu  commyounity    next quad  rendezvous  Yes - First choice   
5  bg2696@nyu.edu     agrilink    next quad     swapbay  Yes - First choice   

   sort_priority  
0              6  
1              6  
2              6  
3              6  
4              3  
5              3

### Project 'commyounity'

...

email                      first      second  \
0   ij2184@nyu.edu                       musi      ascend   
1   dy2262@nyu.edu                       musi  nourishpet   
2   zk2284@nyu.edu                       musi     swapbay   
3   nj2197@nyu.edu         cash me if you can        musi   
4  lhs9817@nyu.edu                   einstein        musi   
5   sg7335@nyu.edu                   einstein        musi   
6   yz8908@nyu.edu  dungeons and distractions        musi   
7  ahc9434@nyu.edu               project crux        musi   

                       third  \
0  dungeons and distractions   
1  dungeons and distractions   
2                commyounity   
3                 engage 2.0   
4                   supermix   
5                   supermix   
6                commyounity   
7                 nourishpet   

                                      voted_for_self  sort_priority  
0                                 Yes - First choice              6  
1  No - I did not select my own project proposal ...              5  
2  No - I did not select my own project proposal ...              5  
3                                 Yes - First choice              3  
4                                 Yes - First choice              3  
5                                 Yes - First choice              3  
6  No - I did not select my own project proposal ...              3  
7                                 Yes - First choice              3

### Project 'supermix'

email     first      second       third      voted_for_self  \
0  vl2289@nyu.edu  supermix  nutrismart  nutrismart  Yes - First choice   
1  sg7335@nyu.edu  einstein        musi    supermix  Yes - First choice   

   sort_priority  
0              6  
1              1

### Project 'einstein'

email     first second     third      voted_for_self  \
0  sg7335@nyu.edu  einstein   musi  supermix  Yes - First choice   

   sort_priority  
0              6

## Verify everything is going well
See the assignments so far.

In [204]:
df_assignments.sample(10)


email       project
5   sad9798@nyu.edu       swapbay
46   jw7677@nyu.edu    cartranker
84   xl4624@nyu.edu   tickerpickr
56  mxf4596@nyu.edu  pocketbudget
33   hs5312@nyu.edu     next quad
58   at4933@nyu.edu  pocketbudget
95   zs1329@nyu.edu      toberead
19  sk10741@nyu.edu          camp
67  gmo6996@nyu.edu   gesturetalk
72   cc7830@nyu.edu    instaskill

Check the number of students already assigned a team.

In [205]:
df_assignments.describe()

email      project
count               105          105
unique              105           20
top     pgl8973@nyu.edu  gesturetalk
freq                  1           10

## Handle remaining students not yet assigned
See which students are not yet assigned a group.

In [206]:
# see who is not yet assigned a project
df_votes

email                      first                    second  \
0    av3114@nyu.edu                roulette go                  strideai   
1   esv2020@nyu.edu                   dinewise                  sanpvite   
2    ea2911@nyu.edu                     ascend              project crux   
3    bg2696@nyu.edu                   agrilink                 next quad   
4    sg7335@nyu.edu                   einstein                      musi   
5    nu2061@nyu.edu                careconnect                  profpick   
6    yz8908@nyu.edu  dungeons and distractions                      musi   
7    yk2154@nyu.edu                roulette go  study space finder @ nyu   
8    vl2289@nyu.edu                   supermix                nutrismart   
9    ajh773@nyu.edu                    stashly                nourishpet   
10  am13367@nyu.edu                    upstore                   swapbay   
11   bb3621@nyu.edu                   agrilink                   upstore   
12   mnm497@nyu.edu                       rirf                nutrismart   
13  ahc9434@nyu.edu               project crux                      musi   

          third                                     voted_for_self  
0      strideai  No - I did not select my own project proposal ...  
1          rirf                                Yes - Second choice  
2      strideai                                 Yes - First choice  
3       swapbay                                 Yes - First choice  
4      supermix                                 Yes - First choice  
5    instaskill                                 Yes - First choice  
6   commyounity  No - I did not select my own project proposal ...  
7    cartranker                                 Yes - First choice  
8    nutrismart                                 Yes - First choice  
9      profpick  No - I did not select my own project proposal ...  
10   instaskill                                 Yes - First choice  
11      stashly                                 Yes - First choice  
12  careconnect                                 Yes - First choice  
13   nourishpet                                 Yes - First choice

See whether any remaining projects have sufficient counts... they shouldn't if we have done our work correctly so far.

In [207]:
# get counts on remaining votes from students who are unsassigned
vote_counts = get_remaining_vote_counts(df_votes).sort_values(by='total', ascending=False)
vote_counts

project  first_count  second_count  third_count  total
26                 nutrismart            0             2            1      3
28                   strideai            0             1            2      3
40                       musi            0             3            0      3
45                    stashly            1             0            1      2
36                    upstore            1             1            0      2
27               project crux            1             1            0      2
38                       rirf            1             0            1      2
39                   profpick            0             1            1      2
23                    swapbay            0             1            1      2
41                   supermix            1             0            1      2
17                   agrilink            2             0            0      2
14                 instaskill            0             0            2      2
16                 nourishpet            0             1            1      2
11                roulette go            2             0            0      2
6                 careconnect            1             0            1      2
4                 commyounity            0             0            1      1
2                   next quad            0             1            0      1
37                   sanpvite            0             1            0      1
42                   einstein            1             0            0      1
48                     ascend            1             0            0      1
21                   dinewise            1             0            0      1
22  dungeons and distractions            1             0            0      1
7                  cartranker            0             0            1      1
5    study space finder @ nyu            0             1            0      1
46                       home            0             0            0      0
35                   toberead            0             0            0      0
50                  studymeta            0             0            0      0
49                     fithub            0             0            0      0
43                over budget            0             0            0      0
47              savings quest            0             0            0      0
33                 engage 2.0            0             0            0      0
44         flavors & fortunes            0             0            0      0
34         cash me if you can            0             0            0      0
0                  rendezvous            0             0            0      0
32                   taskbank            0             0            0      0
31                      spin!            0             0            0      0
3              kitchen helper            0             0            0      0
8        cardwise automations            0             0            0      0
9                pocketbudget            0             0            0      0
10                  tasklatte            0             0            0      0
12                 moodsphere            0             0            0      0
13                gesturetalk            0             0            0      0
15                 vodtracker            0             0            0      0
18                tickerpickr            0             0            0      0
19                    fishdex            0             0            0      0
20          the language café            0             0            0      0
24                       camp            0             0            0      0
25                  roomiehub            0             0            0      0
1                         tbd            0             0            0      0
29                gymflow nyu            0             0            0      0
30              campusconnect            0             0            0      0
51     campus reso

In [208]:
import random
import string

def random_project_name(length=8):
    return 'project_' + ''.join(random.choices(string.ascii_lowercase + string.digits, k=length))
    
# Shuffle df_votes to randomize groupings
df_votes_shuffled = df_votes.sample(frac=1, random_state=42).reset_index(drop=True)

# Split into groups of STUDENTS_PER_TEAM
groups = [
    df_votes_shuffled.iloc[i:i+STUDENTS_PER_TEAM]
    for i in range(0, len(df_votes_shuffled), STUDENTS_PER_TEAM)
]

# Build new dataframe
rows = []
for group in groups:
    project_name = random_project_name()
    for email in group['email']:
        rows.append({'email': email, 'project': project_name})

df_random_teams = pd.DataFrame(rows)
df_random_teams

email           project
0    ajh773@nyu.edu  project_2hh8bfdr
1    bb3621@nyu.edu  project_2hh8bfdr
2    av3114@nyu.edu  project_2hh8bfdr
3    mnm497@nyu.edu  project_2hh8bfdr
4    nu2061@nyu.edu  project_2hh8bfdr
5    vl2289@nyu.edu  project_4z7qaa89
6    ea2911@nyu.edu  project_4z7qaa89
7   esv2020@nyu.edu  project_4z7qaa89
8   ahc9434@nyu.edu  project_4z7qaa89
9    sg7335@nyu.edu  project_4z7qaa89
10   yk2154@nyu.edu  project_946f1ytg
11  am13367@nyu.edu  project_946f1ytg
12   bg2696@nyu.edu  project_946f1ytg
13   yz8908@nyu.edu  project_946f1ytg

Append these last assignments to our dataframe.

In [209]:
df_assignments = pd.concat([df_assignments, df_random_teams], ignore_index=True)
df_assignments.sample(20)

email                   project
23    ab11578@nyu.edu                  taskbank
63     jw7769@nyu.edu                 tasklatte
43    acc7936@nyu.edu  study space finder @ nyu
94    yl10139@nyu.edu                 roomiehub
2     and8979@nyu.edu                   swapbay
7      cp3588@nyu.edu               gesturetalk
81    jls9980@nyu.edu               tickerpickr
31     ns5745@nyu.edu                 next quad
33     hs5312@nyu.edu                 next quad
91    las9963@nyu.edu                 roomiehub
46     jw7677@nyu.edu                cartranker
84     xl4624@nyu.edu               tickerpickr
59   mmc10050@nyu.edu              pocketbudget
17     wc2184@nyu.edu                  taskbank
74     ma8183@nyu.edu                instaskill
115    yk2154@nyu.edu          project_946f1ytg
40    yl10127@nyu.edu  study space finder @ nyu
93    jc11711@nyu.edu                 roomiehub
60     st4850@nyu.edu                 tasklatte
18     mn3497@nyu.edu                      camp

Remove these students from the votes dataframe.

In [210]:
df_votes = df_votes[~df_votes['email'].isin(df_random_teams['email'])].reset_index(drop=True)

Ensure there are no students left unassigned.

In [211]:
df_votes

Empty DataFrame
Columns: [email, first, second, third, voted_for_self]
Index: []

## Save assignments
Save to CSV data file.

In [ ]:
df_assignments.to_csv('data/project_assignments-v1.csv', index=False)